In [1]:
import numpy as np
import pandas as pd
import datetime
import ast
from clickbait import *

### Search for Clickbait Sessions

In [2]:
# Where to look for clickbait datasets
data_dir = f'data/'

# Get session and filenames for directories with .avi files greater than 1gb
datasets, sessions, files = scan_dataset(data_dir, min_size_bytes=1e9, filetype='.avi')

### Load data for a single session.

In [3]:
# Set session index
idx = 0

# Set path and filename prefix
data_path = f"{data_dir}{datasets[idx]}/{sessions[idx]}/{files[idx]}"

# Load video timestamps
video_ts = pd.read_csv(f"{data_path}_video_timestamp.csv")
video_ts.columns = ['timestamp']

# Load events .csv part A
col_names_a = ['trial_number', 'timestamp', 'poke_left', 'poke_right', 'centroid_x', 'centroid_y', 'target_cell']
event_data_a = pd.read_csv(f"{data_path}_eventsA.csv")
event_data_a.columns = col_names_a
pd.to_datetime(event_data_a['timestamp'])

# Load events .csv part B
col_names_b = ['iti', 'water_left', 'reward_state', 'click', 'water_right']
event_data_b = pd.read_csv(f"{data_path}_eventsB.csv")
event_data_b.columns = col_names_b

# Concatenate eventsA abd eventsB dataframes
if len(event_data_a) == len(event_data_b):
    event_data = pd.concat([event_data_a, event_data_b], axis=1)
else:
    print("Event dataframes must contain same number of rows")

#Set types for each column in the dataframe
event_data = event_data.astype({
    'trial_number': 'uint8',
    'timestamp': 'datetime64[ns]',
    'poke_left': 'bool',
    'poke_right': 'bool',
    'centroid_x': 'uint16',
    'centroid_y': 'uint16',
    'target_cell': 'str',
    'iti': 'bool',
    'water_left': 'bool',
    'water_right': 'bool',
    'reward_state': 'bool',
    'click': 'bool'})

# Convert string representations of lists to actual lists
event_data['target_cell'] = event_data['target_cell'].apply(ast.literal_eval)

# Check Lengths of video and events dataframe
print(f"Video length: {len(video_ts)} frames")
print(f"Events Data Length: {len(event_data)} rows")

Video length: 138014 frames
Events Data Length: 297569 rows


### Synch event and video timestamps

In [4]:
# Synchronize events data with video, using nearest matches in the 'timestamp' column 
video_ts['timestamp'] = pd.to_datetime(video_ts['timestamp'])
event_data['timestamp'] = pd.to_datetime(event_data['timestamp'])

# Set 'timestamp' as the index of each dataframe
video_ts = video_ts.set_index('timestamp')
event_data = event_data.set_index('timestamp')

# Map event_data onto the video_data timestamps, using nearest matches between timestamps
event_data = event_data.reindex(video_ts.index, method='nearest')
video_ts = video_ts.reset_index()
event_data = event_data.reset_index()

# Check that event dataframe is the same length as video frames
print(f"Data resampled to match video length:")
print(f"Video length: {len(video_ts)} frames")
print(f"Events Data Length: {len(event_data)} rows")

Data resampled to match video length:
Video length: 138014 frames
Events Data Length: 138014 rows


### Preview Events Dataframe

In [5]:
event_data

timestamp  trial_number  poke_left  poke_right  \
0      2024-11-07 14:46:33.135731200             0      False       False   
1      2024-11-07 14:46:33.155763200             0      False       False   
2      2024-11-07 14:46:33.176409600             0      False       False   
3      2024-11-07 14:46:33.194905600             0      False       False   
4      2024-11-07 14:46:33.212646400             0      False       False   
...                              ...           ...        ...         ...   
138009 2024-11-07 15:32:01.991616000            17      False       False   
138010 2024-11-07 15:32:02.053350400            17      False       False   
138011 2024-11-07 15:32:02.115174400            17      False       False   
138012 2024-11-07 15:32:02.176806400            17      False       False   
138013 2024-11-07 15:32:02.237491200            17      False       False   

        centroid_x  centroid_y target_cell    iti  water_left  reward_state  \
0              528        1794         [3]  False       False         False   
1              527        1794         [3]  False       False         False   
2              528        1795         [3]  False       False         False   
3              529        1795         [3]  False       False         False   
4              530        1794         [3]  False       False         False   
...            ...         ...         ...    ...         ...           ...   
138009         271        1328          []  False        True         False   
138010         261        1317          []  False        True         False   
138011         250        1310          []  False        True         False   
138012         240        1304          []  False        True         False   
138013         233        1297          []  False        True         False   

        click  water_right  
0       False        False  
1       False        False  
2       False        False  
3       False        False  
4       False        False  
...       ...          ...  
138009  False        False  
138010  False        False  
138011  False        False  
138012  False        False  
138013  False        False  

[138014 rows x 12 columns]

### Visualize Trajectories

In [6]:
trials_list = event_data['trial_number'].unique().tolist()
print(trials_list)

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17]


In [7]:
visualize_trial(event_data, trial_number=trials_list, color_code="frame_number", opacity=.1)

In [1]:
from clickbait import *

dim_y = 1952//2
dim_x = 894//2

grid = GridMaze((dim_y,dim_x),(9,4), border=True)

In [2]:
print(grid.cells[1][2][0])

(222, 108)


In [3]:
canvas = np.ones(grid.shape)

grid_img = grid.draw_grid(canvas, color=(0,0,0))

In [4]:
import cv2

cv2.imshow("grid", grid_img)
cv2.waitKey(0)
cv2.destroyAllWindows()